### Maxwell A. Fine
### June 2024

### in order to run `rfifind_stats.py`, you need the `.mask`, `.inf`, and `.stats` files

#### It makes `.zapchans`, `.weights`, `.bandpass` files

This Notebook is for for running `rfifind_stats.py` from `presto` over observations already taken and processed. 

This will make a lot of `.weight` files which we can then use to make a main list of bad freq channels in our data

This is very similar to the other notebook, noise_channels, except this time instead of looking at a single observation we are looking at all with the current (as of writing) observation configuration. 

Then we do a bit of plotting and make a single `.weight` file for the telescope



In [31]:
# imports
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from os.path import basename, dirname
import glob
# we will be running presto in a docker image, so we will execute presto commands using subprocess
import subprocess 
import os

# Define the container name and docker image
container_name = "noise_new_channels_v3"
docker_image = "c7897abba927"
# the local path is different this time
local_path = "/home/afinemax/afinemax/khazad-dum/research/astron_2024/noise_channels/data2/"
container_path = "/data"

# rfifind_stats_params
rfifind_stats_params = ''
# local data path
# cd into data path

# .csv file of filterbankfreqs 
csv_file = 'filterbankfreqs.csv'


In [2]:
ls

bad_channels_.ipynb  data/   files_to_copy.txt
copy_mask_files.sh*  data2/  noise_channels.ipynb


In [3]:
cd data2

/home/afinemax/afinemax/khazad-dum/research/astron_2024/noise_channels/data2


### Read in .scv file and make list of files that have the current settings

In [5]:
# this codw was gifted by Tammo
df = pd.read_csv("filterbankfreqs.csv", sep=" ")

df["basename"] = df["filename"].map(basename)

def get_band(fname):
    s = fname.split("_")
    band_index = s.index("Band")
    return s[band_index - 1]

df["band"] = df["basename"].map(get_band)

df["date"] = df["filename"].map(lambda x: basename(dirname(x)))

lband_filter = (df["nchan"] == 320) & ((df["ch1"] == 1300.0) | (df["ch1"] == 1400.0))
pband_filter = (df["ch1"] == 420)

df_selected = df[lband_filter | pband_filter]

In [6]:
df_selected

filename     ch1  nchan  \
0     /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
1     /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
2     /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
3     /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
4     /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
...                                                 ...     ...    ...   
3467  /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...  1400.0    320   
3468  /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   
3469  /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...  1400.0    320   
3470  /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...  1400.0    320   
3471  /media/camrasdemo/3f3a1b8a-f7dc-4dad-97f4-7b3f...   420.0    160   

                                          basename band        date  
0     FRB20240114A_PV_Band_2024_05_09_06_58_27.fil   PV  2024-05-09  
1     FRB20240114A_PH_Band_2024_05_09_11_39_47.fil   PH  2024-05-09  
2     FRB20240114A_PH_Band_2024_05_09_08_08_43.fil   PH  2024-05-09  
3     FRB20240114A_PV_Band_2024_05_09_07_58_33.fil   PV  2024-05-09  
4     FRB20240114A_PV_Band_2024_05_09_09_43_12.fil   PV  2024-05-09  
...                                            ...  ...         ...  
3467   FRB20220912A_L_Band_2024_01_30_10_40_28.fil    L  2024-01-30  
3468   FRB20240114A_P_Band_2024_01_30_12_17_03.fil    P  2024-01-30  
3469   FRB20240114A_L_Band_2024_01_30_12_57_18.fil    L  2024-01-30  
3470   FRB20240114A_L_Band_2024_01_30_11_19_34.fil    L  2024-01-30  
3471   FRB20220912A_P_Band_2024_01_30_10_40_28.fil    P  2024-01-30  

[2970 rows x 6 columns]

### this is great! Note that 'filename' is the path on mercurius

We want the `*.mask` files so we can make these from the unique basenames, and add a `.mask` col

In [9]:
# Add a new column 'mask_file' based on the 'basename' column
# Remove '.fil' suffix and add a new column 'mask_file'
df_selected.loc[:, 'mask_file'] = df_selected['basename'].str.replace('.fil', '') + '.mask'



In [10]:
df_selected['mask_file']


0       FRB20240114A_PV_Band_2024_05_09_06_58_27.mask
1       FRB20240114A_PH_Band_2024_05_09_11_39_47.mask
2       FRB20240114A_PH_Band_2024_05_09_08_08_43.mask
3       FRB20240114A_PV_Band_2024_05_09_07_58_33.mask
4       FRB20240114A_PV_Band_2024_05_09_09_43_12.mask
                            ...                      
3467     FRB20220912A_L_Band_2024_01_30_10_40_28.mask
3468     FRB20240114A_P_Band_2024_01_30_12_17_03.mask
3469     FRB20240114A_L_Band_2024_01_30_12_57_18.mask
3470     FRB20240114A_L_Band_2024_01_30_11_19_34.mask
3471     FRB20220912A_P_Band_2024_01_30_10_40_28.mask
Name: mask_file, Length: 2970, dtype: object

### Docker Time

In [28]:
# Check if the container already exists
def container_exists(name):
    result = subprocess.run(["docker", "ps", "-a", "--filter", f"name={name}", "--format", "{{.Names}}"], capture_output=True, text=True)
    return name in result.stdout

# Start the container if it exists, otherwise run a new one
if container_exists(container_name):
    subprocess.run(["docker", "start", container_name])
else:
    subprocess.run([
        "docker", "run", "-d", "--name", container_name,
        "-v", f"{local_path}:{container_path}",
        "-e", f"DISPLAY={os.environ['DISPLAY']}",
        "-v", "/tmp/.X11-unix:/tmp/.X11-unix",
        docker_image, "sleep", "infinity"
    ])

# Function to run a command inside the Docker container
def run_command_in_container(command):
    '''Runs command in the docker image cmd line, cmd is a single str'''
    result = subprocess.run(["docker", "exec", container_name, "bash", "-c", command], capture_output=True, text=True)
    return result.stdout, result.stderr

# Example commands to run inside the container

stdout, stderr = run_command_in_container('echo Hello from inside the container!')







noise_new_channels_v3


In [29]:
# we collect all the dirs in our data dir
stdout, stderr = run_command_in_container("ls /data")

dirs = stdout.split('\n') # makes into list of strings

# remove csf_file, and ''
index = dirs.index(csv_file)
dirs.pop(index)

index = dirs.index('')
dirs.pop(index)


print(dirs)



['2024-01-13', '2024-01-17', '2024-01-26', '2024-01-30', '2024-01-31', '2024-02-01', '2024-02-02', '2024-02-04', '2024-02-05', '2024-02-07', '2024-02-08', '2024-02-13', '2024-02-22', '2024-02-29', '2024-03-04', '2024-03-07', '2024-03-09', '2024-03-12', '2024-03-13', '2024-03-14', '2024-03-16', '2024-03-18', '2024-03-19', '2024-03-20', '2024-03-21', '2024-03-22', '2024-03-24', '2024-03-26', '2024-03-27', '2024-03-28', '2024-03-29', '2024-04-03', '2024-04-06', '2024-04-12', '2024-04-16', '2024-04-23', '2024-05-01', '2024-05-04', '2024-05-05', '2024-05-09', '2024-05-25', '2024-06-11']


### now we run rfifind_stats.py on all the `*.mask` files in each dir/process directory

this will make many `*.weights` files in the same path location

There is a memory leak somewhere in this, I can see my ram slowly climb. 
I think maybe it is making plots and not closing them - but I think docker should be killing them after the cmd? What if we turn off x11 forwarding?

Its at ~8gb with all my other windows open

In [53]:
for dir in dirs:
    # ls all the *.mask files
    command = "ls /data/" + dir + "/process/*.mask"
    stdout, stderr = run_command_in_container(command)

    mask_files = stdout.split('\n')

    for mask in mask_files:
        print('Running rfifind_stats.py on ' ,mask)
        command = "rfifind_stats.py " + mask
        stdout, stderr = run_command_in_container(command)
        # print("Standard Output:\n", stdout)
        # print("Standard Error:\n", stderr)

    


Running rfifind_stats.py on  /data/2024-01-13/process/CRAB_L_Band_2024_01_13_15_13_18_rfifind.mask
Standard Output:
 Recommending to zap 28 channels:
  1 channels from Fourier power levels > 200.0
  1 channels from avgs levels being off by > 2.0 sigma
  0 channels from stds levels being off by > 2.0 sigma
  6 channels for being within 0.01 of the band edge
  0 channels were specified by the user
  27 channels for having no variation
  The mask recommends 2 additional bad channels
  adding them to the zap_chans list.

Standard Error:
 
WARNING!:  If raw data have channels in decreasing freq
           order, the channel ordering as given will be
           inverted!  Use 'invertband=True' in 
           write_weights() in that case!
No protocol specified

PGPLOT /xw: cannot connect to X server [:0]
Traceback (most recent call last):
  File "/software/presto5/installation/bin/rfifind_stats.py", line 37, in <module>
    a.set_zap_chans(power=args.fpower,
  File "/usr/local/lib/python3.12/

### Now we want to loop through and load in our `.weights` files

### we only want touse the files that are named in the df 

### End of docker!

 we are going to make a 'master' version with data from all of of them, and then another with data from each dir for ploting purposes 

In [55]:
# We want to loop through dir/process/*.mask in dirs
# want to make a master version, and one for each date

file_directory = 'dirs/process/'
file_extension = '.mask'
file_pattern = file_directory + '*' + file_extension




# the L-band data has 320, the P-band data has 160. Makes a bit of sense, because L-band is 100MHz per file, P-band is 20MHz per file.

# init total files looked at
l_files =0 # have 2 lbands
p_files = 0

# for P-band
try:
    masked_channels_p = None #Pband
    masked_channels_l = None #Lband
    for file in weight_files:
        # load the weight file
        w_data = np.loadtxt(file)

        n_channels = np.shape(w_data[:,0])


        # for P band
        if n_channels == (160,):

            # init master masked_chann array
            if masked_channels_p is None:
                masked_channels_p = np.zeros(shape=np.shape(w_data))

            masked_chan_i = np.asarray([w_data[:, 1] == 0], dtype=float) # 1 if masked, 0 if not masked 
            print('data has n_channels', n_channels)

            masked_channels_p[:,1] += masked_chan_i[0,:]
            p_files +=1


        # for L band 
        if n_channels == (320,):

            # init master masked_chann array
            if masked_channels_l is None:
                masked_channels_l = np.zeros(shape=np.shape(w_data))

            masked_chan_i = np.asarray([w_data[:, 1] == 0], dtype=float) # 1 if masked, 0 if not masked 
            print('data has n_channels', n_channels)

            masked_channels_l[:,1] += masked_chan_i[0,:]
            l_files +=1

except Exception as e:
    print(f"An error occurred: {e}")


['2024-01-13',
 '2024-01-17',
 '2024-01-26',
 '2024-01-30',
 '2024-01-31',
 '2024-02-01',
 '2024-02-02',
 '2024-02-04',
 '2024-02-05',
 '2024-02-07',
 '2024-02-08',
 '2024-02-13',
 '2024-02-22',
 '2024-02-29',
 '2024-03-04',
 '2024-03-07',
 '2024-03-09',
 '2024-03-12',
 '2024-03-13',
 '2024-03-14',
 '2024-03-16',
 '2024-03-18',
 '2024-03-19',
 '2024-03-20',
 '2024-03-21',
 '2024-03-22',
 '2024-03-24',
 '2024-03-26',
 '2024-03-27',
 '2024-03-28',
 '2024-03-29',
 '2024-04-03',
 '2024-04-06',
 '2024-04-12',
 '2024-04-16',
 '2024-04-23',
 '2024-05-01',
 '2024-05-04',
 '2024-05-05',
 '2024-05-09',
 '2024-05-25',
 '2024-06-11']

In [52]:
mask_files[0]

'/data/2024-01-13/process/CRAB_L_Band_2024_01_13_15_13_18_rfifind.mask'